# REIT data analysis workflow

## Intro

This notebook provides a quick walk through on how the Sust Global physical risk dataset can be used for heatmapping based on a collection of asset locations. 

We use the the sample dataset from REIT Data Marketplace and the zonal climate risk stats from Sust Global to show case an example heatmap created with the folium python library.

Reference:
https://app.snowflake.com/marketplace/providers/GZ2FQZOPKR4/REIT%20Data%20Market?dbName=REIT_GEOSPATIAL_ANALYTICS


In [1]:

import os
import geopandas as gpd
import pandas as pd
import numpy as np
import folium
from folium import Map
import json
import contextily as ctx
import matplotlib.pyplot as plt
import xarray as xr
import rioxarray as rio 
from shapely.geometry import Polygon, MultiPolygon, shape, Point

In [2]:
BASE_DATA_FOLDER = './data/'
DOWNLOAD_FOLDER = BASE_DATA_FOLDER+'GEE/'
PLOTS_FOLDER = DOWNLOAD_FOLDER+'plots/'
GEOCODED_DATASET = False
collection_name = 'REIT_DM_sample'
pd.set_option('display.max_rows', 1000)

## Helper Functions

In [3]:
def address_to_geo_iter(df):
    for index, row in df.iterrows():
        try:
            address_string = row['Address'].replace('\n', ' , ')
            geo = geocoder.geocode(address_string)[0]['geometry']
            df.at[index, 'Address'] = address_string
            df.at[index, 'lat'] = geo['lat']
            df.at[index, 'lng'] = geo['lng']
            print(index, address_string, geo['lat'], geo['lng'])
        except:
            df.at[index, 'lat'] = np.NaN
            df.at[index, 'lng'] = np.NaN
            pass

def folium_heatmap(df, hazard):
    index=0
    m = folium.Map([df['lat'].values[0], df['lng'].values[0]], zoom_start=4, tiles='cartodbpositron')
    for point in range(0, df.shape[0]):
            tooltip_label = str(df['Type'].values[point]) + ' : ' + str(df['Entity Name'].values[point]) 
            if pd.isnull(df['lat'].values[point]) or pd.isnull(df['lng'].values[point]):
                print('Null/NaN values')
            else:
                scenario_analytics = df['scenario_analytics'].values[point]
                label = scenario_analytics['ssp585'][hazard]['summary_label']
                if label == 'HIGH':
                    color = 'red'
                elif label == 'MEDIUM':
                    color = 'yellow'
                else:
                    color = 'green'
                folium.CircleMarker([df['lat'].values[point],df['lng'].values[point]], radius=3, color=color, fill=True, fill_opacity=0.8,fill_color=color, popup=tooltip_label).add_to(m)

    return m

## Loading data

Loading data from the REIT DM sample dataset.

In [4]:
df = pd.read_csv(BASE_DATA_FOLDER+'sample_property_data.csv', low_memory=False)
print(df.columns)
print(df.shape)
display(df.head(10))

Index(['REIT', 'QY', 'PROPERTY_ID', 'ATTRIBUTE', 'VALUE'], dtype='object')
(5624579, 5)


REIT      QY  PROPERTY_ID      ATTRIBUTE                             VALUE
0  MAA  Q12023      1023796         COUNTY                           "Duval"
1  MAA  Q12023      1023796       AFFGEOID                  "0500000US12031"
2  EQR  Q12023       289033        ADDRESS                 "810 12th Avenue"
3  EQR  Q12023       289033          STATE                              "WA"
4  MAA  Q12023      1023990           NAME  "Colonial Grand at Wells Branch"
5  MAA  Q12023      1023990          STATE                              "TX"
6  MAA  Q12023      1023990        COUNTRY                              "US"
7  MAA  Q12023      1023990  PROPERTY_TYPE                     "MultiFamily"
8  MAA  Q12023      1023990       AFFGEOID                  "0500000US48453"
9  EQR  Q12023       288913           CITY                       "Watertown"

In [5]:
property_ids = df.PROPERTY_ID.unique().tolist()
len(property_ids)

5095

# Transforming REIT DM propoerty info table

Move from flat list of attributes to quarters and properties and their type/lat/lng attributes

In [6]:
# PROPERTY_TYPE, Y_LAT, X_LONG
df_REIT_prop = pd.DataFrame(columns=['PROPERTY_ID', 'REIT','QY','Type','lat','lng'])

In [7]:
for property_id in property_ids:
    df_prop = df[df['PROPERTY_ID'] == property_id] 
    
    prop_vector = [property_id, 
                   df_prop['REIT'].values[0], 
                   df_prop['QY'].values[0], 
                   df_prop[df_prop['ATTRIBUTE']=='PROPERTY_TYPE']['VALUE'].values[0].strip('"'),
                   df_prop[df_prop['ATTRIBUTE']=='Y_LAT']['VALUE'].values[0],
                   df_prop[df_prop['ATTRIBUTE']=='X_LONG']['VALUE'].values[0]]
    
    df_REIT_prop.loc[len(df_REIT_prop)] = prop_vector

display(df_REIT_prop)

PROPERTY_ID REIT      QY         Type                    lat  \
0         1023796  MAA  Q12023  MultiFamily  3.017505900000000e+01   
1          289033  EQR  Q12023  MultiFamily  4.760956000000000e+01   
2         1023990  MAA  Q12023  MultiFamily  3.043978600000000e+01   
3          288913  EQR  Q12023  MultiFamily  4.236442800000000e+01   
4         1023841  MAA  Q12023  MultiFamily  3.387841400000000e+01   
...           ...  ...     ...          ...                    ...   
5090      1884996  EQR  Q42023  MultiFamily  4.236683500000000e+01   
5091      1884943  EQR  Q42023  MultiFamily  3.441523400000000e+01   
5092      1977703  MAA  Q42023  MultiFamily  2.843532680000000e+01   
5093      1977667  MAA  Q42023  MultiFamily  3.346265000000000e+01   
5094      1977880  MAA  Q42023  MultiFamily  3.014534800000000e+01   

                         lng  
0     -8.160402100000000e+01  
1     -1.223167400000000e+02  
2     -9.767095500000001e+01  
3     -7.118659800000000e+01  
4     -8.432778500000001e+01  
...                      ...  
5090  -7.108436070000000e+01  
5091  -1.185473780000000e+02  
5092  -8.147742839999999e+01  
5093  -1.119228844000000e+02  
5094  -9.780408700000000e+01  

[5095 rows x 6 columns]

# Simple Queries on REIT DM data

- How many properties exist across the dataset?
- How many properties exist in a specific REIT in a specific quarter?
- How many quarters/years are covered? 

In [8]:
len(df_REIT_prop[(df_REIT_prop['QY']=='Q32023') & (df_REIT_prop['REIT']=='EQR')].PROPERTY_ID.unique())

309

In [9]:
df_REIT_prop[(df_REIT_prop['QY']=='Q12023') & (df_REIT_prop['REIT']=='EQR')][:10]

PROPERTY_ID REIT      QY         Type                    lat  \
1        289033  EQR  Q12023  MultiFamily  4.760956000000000e+01   
3        288913  EQR  Q12023  MultiFamily  4.236442800000000e+01   
5        288968  EQR  Q12023  MultiFamily  3.880242700000000e+01   
6        289002  EQR  Q12023  MultiFamily  4.786724500000000e+01   
8        288998  EQR  Q12023  MultiFamily  4.761971900000000e+01   
10       289036  EQR  Q12023  MultiFamily  4.762111900000000e+01   
14       288987  EQR  Q12023  MultiFamily  3.885973600000000e+01   
20       288758  EQR  Q12023  MultiFamily  3.378988900000000e+01   
21       288962  EQR  Q12023  MultiFamily  3.298899510000000e+01   
25       288904  EQR  Q12023  MultiFamily  4.236546300000000e+01   

                       lng  
1   -1.223167400000000e+02  
3   -7.118659800000000e+01  
5   -7.712242000000001e+01  
6   -1.222188840000000e+02  
8   -1.223221500000000e+02  
10  -1.223593290000000e+02  
14  -7.705493600000000e+01  
20  -1.181473610000000e+02  
21  -9.683128130000000e+01  
25  -7.108261899999999e+01

In [10]:
df_REIT_prop.QY.unique()

array(['Q12023', 'Q32022', 'Q22022', 'Q42022', 'Q22023', 'Q42023',
       'Q12024', 'Q32023'], dtype=object)

# Transform to a geodataframe

In [11]:
gdf_REIT_prop = gpd.GeoDataFrame(df_REIT_prop, geometry=gpd.points_from_xy(df_REIT_prop.lng, df_REIT_prop.lat))
gdf_REIT_prop = gdf_REIT_prop.set_crs("epsg:4326", inplace = True)
print(gdf_REIT_prop.crs)
print(gdf_REIT_prop.shape)

epsg:4326
(5095, 7)


# Load up zonal stats dataset from Sust Global

we use admin 3 for the US here (zip codes)

In [17]:
src = BASE_DATA_FOLDER + 'USA_3.geojson'

gdf = gpd.read_file(src)
print(gdf.shape)
print(gdf.crs)
display(gdf[:10])

(3234, 14)
EPSG:4326


scenario_analytics    id entity_id  \
0  {'ssp585': {'wildfire': {'summary_score': 0, '...     0             
1  {'ssp585': {'wildfire': {'summary_score': 0.00...     1             
2  {'ssp585': {'wildfire': {'summary_score': 0, '...    10             
3  {'ssp585': {'wildfire': {'summary_score': 0, '...   100             
4  {'ssp585': {'wildfire': {'summary_score': 0, '...  1000             
5  {'ssp585': {'wildfire': {'summary_score': 0, '...  1001             
6  {'ssp585': {'wildfire': {'summary_score': 0, '...  1002             
7  {'ssp585': {'wildfire': {'summary_score': 0.00...  1003             
8  {'ssp585': {'wildfire': {'summary_score': 0, '...  1004             
9  {'ssp585': {'wildfire': {'summary_score': 0.01...  1005             

  entity_name                                             labels         lng  \
0              {'label:fid': 1, 'label:LSAD': '06', 'label:NA...   -81.74317   
1              {'label:fid': 2, 'label:LSAD': '06', 'label:NA...   -84.46701   
2              {'label:fid': 11, 'label:LSAD': '06', 'label:N...   -83.56637   
3              {'label:fid': 101, 'label:LSAD': '06', 'label:...   -83.42110   
4              {'label:fid': 1001, 'label:LSAD': '06', 'label...  -123.09834   
5              {'label:fid': 1002, 'label:LSAD': '06', 'label...  -118.88687   
6              {'label:fid': 1003, 'label:LSAD': '06', 'label...   -91.10702   
7              {'label:fid': 1004, 'label:LSAD': '06', 'label...   -93.66842   
8              {'label:fid': 1005, 'label:LSAD': '06', 'label...   -94.27433   
9              {'label:fid': 1006, 'label:LSAD': '06', 'label...  -120.51611   

        lat admin_processing_level admin0      admin1 admin2 admin3 admin4  \
0  32.39681                      2    USA     Georgia  13031                 
1  33.79024                      2    USA     Georgia  13121                 
2  34.13387                      2    USA     Georgia  13157                 
3  38.19625                      2    USA    Kentucky  21205                 
4  45.56007                      2    USA      Oregon  41067                 
5  37.93910                      2    USA  California  06051                 
6  36.04122                      2    USA    Arkansas  05075                 
7  33.73538                      2    USA    Arkansas  05057                 
8  35.19884                      2    USA    Arkansas  05131                 
9  39.58037                      2    USA  California  06091                 

                                            geometry  
0  POLYGON ((-82.02684 32.55516, -82.03023 32.538...  
1  POLYGON ((-84.84931 33.51318, -84.85071 33.511...  
2  POLYGON ((-83.81768 34.12749, -83.81600 34.126...  
3  POLYGON ((-83.63517 38.19025, -83.63519 38.187...  
4  POLYGON ((-123.48544 45.44713, -123.48608 45.4...  
5  POLYGON ((-119.64893 38.28913, -119.65137 38.2...  
6  POLYGON ((-91.35694 35.90519, -91.35742 35.890...  
7  POLYGON ((-93.96945 33.74021, -93.96855 33.737...  
8  POLYGON ((-94.44760 34.94192, -94.44789 34.934...  
9  POLYGON ((-121.05748 39.53999, -121.05821 39.5...

In [18]:
gdf['scenario_analytics'][0]

{'ssp585': {'wildfire': {'summary_score': 0,
   'summary_label': 'LOW',
   'indicator_baseline': 0,
   'indicator_baseline_lbd': 0,
   'indicator_baseline_ubd': 0,
   'indicator_2030': 0,
   'indicator_2030_lbd': 0,
   'indicator_2030_ubd': 0,
   'indicator_2050': 0,
   'indicator_2050_lbd': 0,
   'indicator_2050_ubd': 0,
   'indicator_2080': 0,
   'indicator_2080_lbd': 0,
   'indicator_2080_ubd': 0,
   'structural_damage_baseline': 0,
   'structural_damage_baseline_lbd': 0,
   'structural_damage_baseline_ubd': 0,
   'structural_damage_2030': 0,
   'structural_damage_2030_lbd': 0,
   'structural_damage_2030_ubd': 0,
   'structural_damage_2050': 0,
   'structural_damage_2050_lbd': 0,
   'structural_damage_2050_ubd': 0,
   'structural_damage_2080': 0,
   'structural_damage_2080_lbd': 0,
   'structural_damage_2080_ubd': 0,
   'business_interruption_baseline': 0,
   'business_interruption_baseline_lbd': 0,
   'business_interruption_baseline_ubd': 0,
   'business_interruption_2030': 0,
   '

# Run a spatial join to get risk metadata for each property 

The spatial join will append risk data to the asset dataframe depending on the zone they fall in.

In [20]:
gdf_REIT_risk = gpd.sjoin(gdf_REIT_prop, gdf, predicate='within')
print(gdf_REIT_risk.shape)
gdf_REIT_risk.rename(columns={'lat_left':'lat', 'lng_left':'lng', 'PROPERTY_ID':'Entity Name'}, inplace=True)
display(gdf_REIT_risk.head(10))

(5095, 21)


Entity Name REIT      QY         Type                    lat  \
0      1023796  MAA  Q12023  MultiFamily  3.017505900000000e+01   
1       289033  EQR  Q12023  MultiFamily  4.760956000000000e+01   
2      1023990  MAA  Q12023  MultiFamily  3.043978600000000e+01   
3       288913  EQR  Q12023  MultiFamily  4.236442800000000e+01   
4      1023841  MAA  Q12023  MultiFamily  3.387841400000000e+01   
5       288968  EQR  Q12023  MultiFamily  3.880242700000000e+01   
6       289002  EQR  Q12023  MultiFamily  4.786724500000000e+01   
7      1024079  MAA  Q12023  MultiFamily  3.745347100000000e+01   
8       288998  EQR  Q12023  MultiFamily  4.761971900000000e+01   
9      1024073  MAA  Q12023  MultiFamily  3.829450340000000e+01   

                      lng                     geometry  index_right  \
0  -8.160402100000000e+01   POINT (-81.60402 30.17506)         3032   
1  -1.223167400000000e+02  POINT (-122.31674 47.60956)          107   
2  -9.767095500000001e+01   POINT (-97.67096 30.43979)         2794   
3  -7.118659800000000e+01   POINT (-71.18660 42.36443)         2842   
4  -8.432778500000001e+01   POINT (-84.32779 33.87841)         2992   
5  -7.712242000000001e+01   POINT (-77.12242 38.80243)         1388   
6  -1.222188840000000e+02  POINT (-122.21888 47.86724)         3071   
7  -7.764581000000000e+01   POINT (-77.64581 37.45347)         1603   
8  -1.223221500000000e+02  POINT (-122.32215 47.61972)          107   
9  -7.746350590000000e+01   POINT (-77.46351 38.29450)         3163   

                                  scenario_analytics    id  ... entity_name  \
0  {'ssp585': {'wildfire': {'summary_score': 0, '...   817  ...               
1  {'ssp585': {'wildfire': {'summary_score': 0.00...  1094  ...               
2  {'ssp585': {'wildfire': {'summary_score': 0, '...   602  ...               
3  {'ssp585': {'wildfire': {'summary_score': 0, '...   646  ...               
4  {'ssp585': {'wildfire': {'summary_score': 0, '...   781  ...               
5  {'ssp585': {'wildfire': {'summary_score': 0.00...  2247  ...               
6  {'ssp585': {'wildfire': {'summary_score': 0.00...   852  ...               
7  {'ssp585': {'wildfire': {'summary_score': 0.00...  2440  ...               
8  {'ssp585': {'wildfire': {'summary_score': 0.00...  1094  ...               
9  {'ssp585': {'wildfire': {'summary_score': 0, '...   935  ...               

                                              labels   lng_right lat_right  \
0  {'label:fid': 818, 'label:LSAD': '06', 'label:...   -81.67144  30.33130   
1  {'label:fid': 1095, 'label:LSAD': '06', 'label...  -121.80523  47.49025   
2  {'label:fid': 603, 'label:LSAD': '06', 'label:...   -97.78196  30.33437   
3  {'label:fid': 647, 'label:LSAD': '06', 'label:...   -71.39181  42.48557   
4  {'label:fid': 782, 'label:LSAD': '06', 'label:...   -84.22643  33.77154   
5  {'label:fid': 2248, 'label:LSAD': '25', 'label...   -77.08614  38.81849   
6  {'label:fid': 853, 'label:LSAD': '06', 'label:...  -121.69719  48.04736   
7  {'label:fid': 2441, 'label:LSAD': '06', 'label...   -77.58694  37.37853   
8  {'label:fid': 1095, 'label:LSAD': '06', 'label...  -121.80523  47.49025   
9  {'label:fid': 936, 'label:LSAD': '25', 'label:...   -77.48719  38.29920   

  admin_processing_level admin0         admin1 admin2 admin3 admin4  
0                      2    USA        Florida  12031                
1                      2    USA     Washington  53033                
2                      2    USA          Texas  48453                
3                      2    USA  Massachusetts  25017                
4                      2    USA        Georgia  13089                
5                      2    USA       Virginia  51510                
6                      2    USA     Washington  53061                
7                      2    USA       Virginia  51041                
8                      2    USA     Washington  53033                
9                      2    USA       Virginia  51630 

# Plot on slippy map as heatmap

You can pass hazard value as one of the following: 'wildfire', 'flood', 'cyclone', 'heatwave', 'sea_level_rise', 'water_stress'.

In [21]:
m = folium_heatmap(gdf_REIT_risk, 'sea_level_rise')
m